In [1]:
import pandas as pd
import numpy as np 
import glob
import os 

from datetime import datetime
from openpyxl import load_workbook
from openpyxl.styles import PatternFill, Font

In [2]:
hoje = datetime.today().strftime('%Y-%m-%d')

In [9]:
calendario = pd.read_excel(r"..\\..\\SUPRIMENTOS\BD_LANÇAMENTOS\BOT\arquivos usados por todos os lançamentos\Ciclo_Expandido_com_Datas.xlsx")

calendario['Date'] = pd.to_datetime(calendario['Date'])

# Get today (normalized to midnight)
today = pd.Timestamp("today").normalize()

calendario['NUM_CICLO'] = calendario['Ciclo'].str[-2:].astype(int)

calendario['ANO_CICLO'] = calendario['Ciclo'].str[0:5]

calendario = calendario[calendario['MARCA'] == "BOTICARIO"]

calendario['CICLOMAIS2'] = calendario['ANO_CICLO'].astype(str) + (calendario['NUM_CICLO'].astype(int) + 2).astype(str).str.zfill(2)       #<<< MUDAR O "4" (CICLO ATUAL + 4 PARA ACHAR O CICLO DA SUGESTÃO) EX: C202505 -> C202509
ciclo_mais2 = calendario[calendario['Date'].dt.normalize() == today]['CICLOMAIS2'].iloc[0]

# Filter rows where date matches today
filtered_calendario = calendario[calendario['Ciclo'] == ciclo_mais2][:1]

filtered_calendario['dias_ate_inicio'] = filtered_calendario['INICIO CICLO'].iloc[0] - today

filtered_calendario['dias_ate_inicio'] = filtered_calendario['dias_ate_inicio'].dt.days.astype(int)

filtered_calendario['match'] = 1


In [11]:
filtered_calendario

Ciclo INICIO CICLO  FIM CICLO  DURAÇÃO      MARCA       Date  \
2507  C202517   2025-12-01 2025-12-25       25  BOTICARIO 2025-12-01   

      NUM_CICLO ANO_CICLO CICLOMAIS2  dias_ate_inicio  match  
2507         17     C2025    C202519               45      1

In [12]:
ciclo_lanc = filtered_calendario['Ciclo'].max()

In [13]:
ciclo_lanc

'C202517'

In [15]:
#COLOCAR ARQUIVO SIMILAR AQUI (ALTERAR)

arquivo_similares = r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BOT\BOT - C17\arquivos para geração da sugestão\similar novo splash\PRODUTOS SIMILARES - BOT(body splash).xlsx"

df_similares = pd.read_excel(arquivo_similares)

df_similares = pd.merge(left=df_similares,right=calendario[['Ciclo','INICIO CICLO','FIM CICLO','DURAÇÃO']], how= 'left', left_on = 'CICLO SIMILAR',right_on = 'Ciclo' )

df_similares = df_similares.drop(columns=['Ciclo'])

df_similares = df_similares.rename(columns={'INICIO CICLO':'INICIO CICLO SIMILAR','FIM CICLO':'FIM CICLO SIMILAR','DURAÇÃO':'DURAÇÃO CICLO SIMILAR'})
df_similares.drop_duplicates(inplace=True)

df_similares['MATCH'] = 1

df_similares = df_similares.drop(columns=['INICIO DO CICLO', 'FIM DO CICLO', 'DURAÇÃO CICLO','INICIO CICLO SIMILAR','FIM CICLO SIMILAR','DURAÇÃO CICLO SIMILAR'])

In [16]:
df_similares.head()

PRODUTO LANÇAMENTO                            DESCRIÇÃO DO LANÇAMENTO  \
0               86116  CUIDE-SE BEM DOCES DELÍRIOS ALGODÃO DOCE BODY ...   

   PRODUTO SIMILAR                                  DESCRIÇÃO SIMILAR  \
0            58363  Body Splash Desodrante Colônia Cuide-se Bem Nu...   

  CICLO SIMILAR FOCO  IAF   CATEGORIA         MARCA % CONSUMIDOR  \
0       C202506  Não  Não  PERFUMARIA  CUIDE-SE BEM            -   

  MECANICA CONSUMIDOR % REVENDEDOR MECANICA REVENDEDOR TIPO DE PRODUTO  MATCH  
0                   -            -                   -         REGULAR      1

In [17]:
#TRANSFORMA A COLUNA EM STRING
df_similares['PRODUTO SIMILAR'] = df_similares['PRODUTO SIMILAR'].astype('str')
# TIRA O '.0' DO FIM SE OCORRER
df_similares['PRODUTO SIMILAR'] = df_similares['PRODUTO SIMILAR'].replace(r'\.0$', '', regex=True)




In [19]:
# SEMPRE COLOCAR O DO USUARIO.(ALTERAR)
df_tabela = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BOT\BOT - C17\arquivos para geração da sugestão\TABELA DE PEDIDO\Pedidos Semanais Especiais - BOT - 202517.xlsx")

# FILTRA REGIÃO = NORDESTE
df_tabela = df_tabela[df_tabela['Região'] == 'NNE'] 
# TIRA CANAL ECOMERCE DO PLANILHA
df_tabela = df_tabela[(df_tabela['Canal'] != 'Ecomm') | (df_tabela['Canal'] != 'Ecomm | VD') | (df_tabela['Canal'] != 'Ecomm | Loja')] 
# UNIFICA DESCONTOS CANAL LOJA
df_tabela['Canal'] = np.where((df_tabela['Canal'] == "Loja") | (df_tabela['Canal'] == "Todos") | (df_tabela['Canal'] == "Loja | VD"),"TODOS","VD")
# SÓ MANTÉM LANÇAMENTOS 
df_tabela = df_tabela[df_tabela['Tipo de promoção'].str.contains('Lançamentos', na=False)]

In [20]:
df_pdv = pd.read_excel(r"..\\..\\SUPRIMENTOS\BD_LANÇAMENTOS\BOT\BOT - C16\arquivos para geração da sugestão\PDV\PDV_ATT.xlsx")
# remove lojas QDB
df_pdv = df_pdv[~df_pdv['PDV'].isin([910173, 910291])]

#feito para retificar os UFS ao fim do script
df_pdv_origi = pd.read_excel(r"..\\..\\SUPRIMENTOS\BD_LANÇAMENTOS\BOT\BOT - C16\arquivos para geração da sugestão\PDV\PDV_ATT.xlsx")
df_pdv_origi = df_pdv_origi[~df_pdv_origi['PDV'].isin([910173, 910291])]

In [21]:
df_pdv

PDV CANAL                     DESCRIÇÃO  \
0   23156    LJ           SHOPPING CENTRO SUL   
1    4494   MTZ                    ESCRITORIO   
2    1137   MTZ                           AMG   
3   12522    LJ               MACEIO SHOP EXP   
4   12817    LJ                SHOPPING PATIO   
..    ...   ...                           ...   
79  24257   HIB                 Miguel Calmon   
80  24268    LJ          COMERCIO-LJ JACOBINA   
81  24269    VD          COMERCIO-ER JACOBINA   
82  24293   HIB  COMERCIO-HIB MORRO DO CHAPEU   
85  23813   HIB                       VALENTE   

                                PDV DESC     REGIÃO   ESTADO  CIDADE   UF  \
0                                    NaN        NaN  SERGIPE     NaN   SE   
1       4494-COMERCIO-PONTA VERDE-MACEIO         ND  ALAGOAS  MACEIÓ   AL   
2                      1137-AMG SERRARIA         ND  ALAGOAS  MACEIÓ   AL   
3   12522-COMERCIO -MACEIO SHOP EXPANSAO  MCZ BAIXA  ALAGOAS  MACEIÓ   AL   
4         12817-COMERCIO -SHOPPING PATIO   MCZ ALTA  ALAGOAS  MACEIÓ   AL   
..                                   ...        ...      ...     ...  ...   
79                                   NaN        NaN      NaN     NaN  BA3   
80                                   NaN        NaN      NaN     NaN  BA3   
81                                   NaN        NaN      NaN     NaN  BA3   
82                                   NaN        NaN      NaN     NaN  BA3   
85                                   NaN        NaN      NaN     NaN   BA   

          MARCA   ANALISTA           GESTÃO          SUPERVISOR   STATUS  \
0           NaN    Inativa          Inativa             Inativa  INATIVO   
1    CP GINSENG    Inativa          Inativa             Inativa  INATIVO   
2   O BOTICARIO    Inativa          Inativa             Inativa  INATIVO   
3   O BOTICARIO       LUAN      Betina Melo  Efigênia Herculano    ATIVO   
4   O BOTICARIO  JEFFERSON  Pamella Barbosa      Maxwell Vieira    ATIVO   
..          ...        ...              ...                 ...      ...   
79  O BOTICARIO   THAYLLAN       Caio Luna             FERNANDA    ATIVO   
80  O BOTICARIO   THAYLLAN       Caio Luna             FERNANDA    ATIVO   
81  O BOTICARIO  JEFFERSON       Caio Luna             FERNANDA    ATIVO   
82  O BOTICARIO   MARCYARA          Alysson            FERNANDA    ATIVO   
85  O BOTICARIO   MARCYARA              NaN             CLÁUDIA    ATIVO   

   ANALISTA EUD  
0          LOJA  
1       INATIVO  
2       INATIVO  
3          LOJA  
4          LOJA  
..          ...  
79         HARY  
80         LOJA  
81         HARY  
82       DIELLY  
85         HARY  

[84 rows x 14 columns]

In [22]:

#trativa de dados

df_pdv = df_pdv.rename(columns={'DESCRIÇÃO':'DESCRIÇÃO PDV'})

df_pdv = df_pdv.drop(columns=['REGIÃO', 'ESTADO','CIDADE','GESTÃO','MARCA'])

df_pdv['UF'] = np.where((df_pdv['UF'] == 'VDC') | (df_pdv['UF'] == 'BA3'),'BA',df_pdv['UF'])

df_pdv = df_pdv[df_pdv['STATUS'] != "INATIVO"]

df_pdv = df_pdv[df_pdv['STATUS'] != "MATRIZ"]

df_pdv = df_pdv[df_pdv['SUPERVISOR'] != 'Inativa']

df_pdv['MATCH'] = 1

In [23]:
# DISTRIBUINDO OS PDVS PARA OS SIMILARES
df_similares = pd.merge(left=df_similares,right=df_pdv,right_on=['MATCH'],left_on=['MATCH'],how='inner')

df_similares = df_similares.drop_duplicates()

In [24]:
#CHECAGEM DE QTD PDVS POR PRODUTO LANÇAMENTO.
df_similares['PRODUTO LANÇAMENTO'].value_counts()

PRODUTO LANÇAMENTO
86116    76
Name: count, dtype: int64

In [25]:
import pyodbc
import configparser

#query de vendas por ciclo

config = configparser.ConfigParser()
config.read(r"../../SUPRIMENTOS/BD_LANÇAMENTOS/BOT/arquivos usados por todos os lançamentos/credenciais.ini")

conn = pyodbc.connect(
    f"DRIVER={{SQL Server}};"
    f"SERVER={config['banco']['host']},1433;"
    f"DATABASE=GINSENG;"
    f"UID={config['banco']['user']};"
    f"PWD={config['banco']['password']}"
)

query = f'''
SELECT 
    B.PDV, 
    B.SKU,
    bd.SKU2, 
    COALESCE(bd.SKU2, b.SKU) AS SKU_FINAL,
    B.DESCRICAO,
    SUM(CAST(b.VENDAS AS DECIMAL(18,2))) AS VENDAS_CICLO,
    C.Ciclo
FROM base_vendas_bi b
INNER JOIN ciclos_data_2025 c 
    ON CAST(b.[DATA] AS DATE) = CONVERT(DATE, c.[Date], 103) AND C.MARCA = 'BOT'
LEFT JOIN base_depara bd on b.SKU = bd.SKU 
WHERE CAST(b.[DATA] AS DATE) >= DATEADD(YEAR, -1, GETDATE())
GROUP BY
    B.PDV, 
    B.SKU,
    bd.SKU2,
    B.DESCRICAO,
    C.Ciclo
HAVING SUM(CAST(b.VENDAS AS DECIMAL(18,2))) > 0
'''
dfi = pd.read_sql_query(query, conn)
conn.close()

dfi['SKU2'] = dfi['SKU2'].fillna("-")


C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_28176\3630339320.py:39: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  dfi = pd.read_sql_query(query, conn)


In [26]:

# 1. Agrupamento horizontalizando as vendas por ciclo. transformando coluna de cilos em cada ciclo por coluna.
df_agrupado = dfi.groupby(['PDV', 'SKU_FINAL', 'DESCRICAO', 'Ciclo'], as_index=False)['VENDAS_CICLO'].sum()

# 2. Pivotar o DataFrame
df_pivotado = df_agrupado.pivot_table(
    index=['PDV', 'SKU_FINAL', 'DESCRICAO'],
    columns='Ciclo',
    values='VENDAS_CICLO',
    fill_value=0  # Substitui NaN por 0
)

# 3. Resetar o índice para deixar como DataFrame normal (opcional)
df_pivotadowawa = df_pivotado.reset_index()

# 4. (Opcional) Renomear colunas com prefixo "Ciclo_"
df_pivotadowawa.columns.name = None
df_pivotadowawa = df_pivotadowawa.rename(columns=lambda x: f'Ciclo_{x}' if isinstance(x, (int, str)) and str(x).isdigit() else x)

# Resultado final
df_pivotadowawa.head()

PDV  SKU_FINAL                             DESCRICAO  C202415  C202416  \
0  12522       1080  INTENSE GLOS LAB BUBBAL TUT/FRUT 5ml      0.0     10.0   
1  12522       1296   PMPCK THE BLEND DES ANTIT AER 2x75g      3.0      2.0   
2  12522       1302        PMPCK LILY DES ANTIT AER 2x75g      5.0      6.0   
3  12522       1314        PMPCK ZAAD DES ANTIT AER 2x75g      1.0      1.0   
4  12522       1317      PMPCK MALBEC DES ANTIT AER 2x75g      2.0      5.0   

   C202417  C202501  C202502  C202503  C202504  ...  C202506  C202507  \
0      2.0      2.0      1.0      2.0      3.0  ...      7.0     17.0   
1      0.0      0.0      0.0      0.0      0.0  ...      0.0      0.0   
2      0.0      0.0      0.0      0.0      0.0  ...      3.0      4.0   
3      0.0      0.0      0.0      0.0      0.0  ...      0.0      0.0   
4      0.0      1.0      3.0      0.0      0.0  ...      1.0      1.0   

   C202508  C202509  C202510  C202511  C202512  C202513  C202514  C202515  
0      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0  
1      0.0      0.0      0.0      0.0      0.0      2.0      1.0      0.0  
2      0.0      4.0      4.0      2.0      1.0      6.0      0.0      0.0  
3      0.0      0.0      0.0      1.0      1.0      1.0      0.0      0.0  
4      0.0      2.0      2.0      3.0      2.0      5.0      0.0      0.0  

[5 rows x 21 columns]

In [27]:
import pandas as pd
print(pd.__version__)


2.2.3


In [28]:
conn = pyodbc.connect(
    f"DRIVER={{SQL Server}};"
    f"SERVER={config['banco']['host']},1433;"
    f"DATABASE=GINSENG;"
    f"UID={config['banco']['user']};"
    f"PWD={config['banco']['password']}"
)

query_est_draft = f'''
select em.PDV ,
COALESCE(cast(em.SKU_PARA as int) , cast(em.SKU as int)) as SKU,
em.DESCRICAO,
d.salescurve as curva,
d.codcategory as categoria,
d.nextcycleprojection as proj_mar
,d.secondtonextcycleprojection as 'proj_mar+1',
em.[ESTOQUE ATUAL],em.[ESTOQUE EM TRANSITO],
em.[PEDIDO PENDENTE],
em.[DDV PREVISTO] ,
d.pricesellin as 'preço'
from estoque_mar em 
left join draft d on d.code = COALESCE(cast(em.SKU_PARA as int) , cast(em.SKU as int)) and d.loja_id = em.PDV 
where em.ORIGEM = 'BOT'
'''
df_draft_ = pd.read_sql(query_est_draft, conn)
conn.close()



C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_28176\3920982216.py:25: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df_draft_ = pd.read_sql(query_est_draft, conn)


In [29]:
df_draft = df_draft_

In [30]:
df_draft.head()

PDV    SKU                                 DESCRICAO curva  categoria  \
0  20998  57438   MAKE B BAT GLOSS C/AC POLIGL CORAL 3,6g     E  MAQUIAGEM   
1  20998  81628    MAKE B BAT GLOSS C/AC POLIGL NUDE 3,6g     C  MAQUIAGEM   
2  20998  81621  MAKE B BAT MATE C/AC POLIG ORANGE FEV 4g     C  MAQUIAGEM   
3  20998  55984  MAKE B BAT ST/PREN HYAL CAND TOF V3 3,4g     C  MAQUIAGEM   
4  20998  58566     MAKE B CORRET LIQ FAC EFFECT 10 5,7ml     C  MAQUIAGEM   

   proj_mar  proj_mar+1  ESTOQUE ATUAL  ESTOQUE EM TRANSITO  PEDIDO PENDENTE  \
0       1.0         3.0            0.0                  0.0              0.0   
1       1.0         0.0            1.0                  0.0              0.0   
2       0.0         0.0           10.0                  0.0              0.0   
3       1.0         0.0            9.0                  0.0              0.0   
4       2.0         1.0            0.0                  1.0              1.0   

  DDV PREVISTO  preço  
0         0,04  18.29  
1         0,02  18.29  
2            0  16.66  
3         0,02  21.67  
4         None  15.30

In [31]:
# REMOVENDO OUI DOS PRODUTOS BOTI
df_draft = df_draft[~df_draft['DESCRICAO'].str.contains('OUI', na=False)]

df_draft['ESTOQUE ATUAL'] = df_draft['ESTOQUE ATUAL'].astype(float)

df_draft['ESTOQUE EM TRANSITO'] = df_draft['ESTOQUE EM TRANSITO'].astype(float)

df_draft['PEDIDO PENDENTE'] = df_draft['PEDIDO PENDENTE'].astype(float)

df_draft.shape

C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_28176\2417376295.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_draft['ESTOQUE ATUAL'] = df_draft['ESTOQUE ATUAL'].astype(float)
C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_28176\2417376295.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_draft['ESTOQUE EM TRANSITO'] = df_draft['ESTOQUE EM TRANSITO'].astype(float)
C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_28176\2417376295.py:8: SettingWithCopyWarning: 
A value is trying t

(278761, 12)

In [32]:
df_draft['DDV PREVISTO'] = df_draft['DDV PREVISTO'].str.replace(',','.')

df_draft['DDV PREVISTO'] = df_draft['DDV PREVISTO'].astype(float)

df_draft['DDV PREVISTO'] = df_draft['DDV PREVISTO'].fillna(0)

C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_28176\1952797845.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_draft['DDV PREVISTO'] = df_draft['DDV PREVISTO'].str.replace(',','.')
C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_28176\1952797845.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_draft['DDV PREVISTO'] = df_draft['DDV PREVISTO'].astype(float)
C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_28176\1952797845.py:5: SettingWithCopyWarning: 
A value is trying to be set 

In [33]:
#agrupamento pra evitar duplicidade
df_draft = df_draft.groupby(['PDV','SKU','curva','categoria'])[['proj_mar','proj_mar+1','ESTOQUE ATUAL','ESTOQUE EM TRANSITO','PEDIDO PENDENTE','DDV PREVISTO','preço']].max().reset_index()

In [34]:
df_draft['SKU'] = df_draft['SKU'].astype('Int64')

In [35]:
df_draft = pd.merge(df_draft,df_pivotadowawa,left_on=['PDV','SKU'],right_on=['PDV','SKU_FINAL'],how='inner')

In [36]:
# OLHO COLUNAS DE VENDA
df_draft.columns[13:31]

Index(['C202415', 'C202416', 'C202417', 'C202501', 'C202502', 'C202503',
       'C202504', 'C202505', 'C202506', 'C202507', 'C202508', 'C202509',
       'C202510', 'C202511', 'C202512', 'C202513', 'C202514', 'C202515'],
      dtype='object')

In [37]:
# Define as colunas mensais
colunas_mensais = df_draft.columns[13:31]

# Agrupa por PDV e calcula crescimento médio por PDV
def calcular_crescimento(grupo):
    soma_mensal = grupo[colunas_mensais].sum()             # soma por mês
    variacao_mensal = soma_mensal.pct_change().dropna()    # variação percentual mês a mês
    variacao_mensal = variacao_mensal[np.isfinite(variacao_mensal)]

    if len(variacao_mensal) == 0:
        return pd.Series({'CRESCIMENTO': np.nan})

    media = variacao_mensal.mean()
    desvio = variacao_mensal.std()

    limite_sup = media + 2 * desvio
    limite_inf = media - 2 * desvio

    variacoes_filtradas = variacao_mensal[variacao_mensal.between(limite_inf, limite_sup)]
    crescimento = round(variacoes_filtradas.mean(), 4)
    return pd.Series({'CRESCIMENTO': crescimento})

# Aplica a função por PDV
crescimento_por_pdv = df_draft.groupby('PDV').apply(calcular_crescimento)

# Merge do resultado de volta no dataframe original
df_draft = df_draft.merge(crescimento_por_pdv, on='PDV', how='left')


C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_28176\1731143361.py:24: DeprecationWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  crescimento_por_pdv = df_draft.groupby('PDV').apply(calcular_crescimento)


In [38]:
df_similares['PRODUTO SIMILAR'] = df_similares['PRODUTO SIMILAR'].astype('Int64')
df_similares['PRODUTO SIMILAR'].head()

0    58363
1    58363
2    58363
3    58363
4    58363
Name: PRODUTO SIMILAR, dtype: Int64

In [39]:
df_draft[['PDV', 'SKU']].dtypes

PDV    object
SKU     Int64
dtype: object

In [40]:
df_draft['PDV'] = df_draft['PDV'].astype('Int64')

df_final = pd.merge(left=df_similares,right=df_draft,right_on=['PDV', 'SKU'],left_on=['PDV','PRODUTO SIMILAR'],how='left')

In [41]:
df_similares= df_similares[df_similares['PRODUTO SIMILAR'].notna()]

df_similares['PRODUTO SIMILAR'].value_counts()

PRODUTO SIMILAR
58363    76
Name: count, dtype: Int64

In [42]:
df_final['SKU'].value_counts()

SKU
58363    75
Name: count, dtype: Int64

In [43]:
df_venda_diaria = pd.read_csv(
    r"../../SUPRIMENTOS/BD_LANÇAMENTOS/BOT/arquivos usados por todos os lançamentos/vendas 20250815.csv",
    sep=';',
    dtype={'SKU_2': str},decimal=',')

In [44]:
df_venda_diaria['VENDAS_CICLO'] = df_venda_diaria['VENDAS_CICLO'].str.replace(r'\.', '', regex=True)

In [45]:
df_venda_diaria.head()

PDV     SKU                                 DESCRICAO VENDAS_CICLO  \
0  12522  51.944     COFFEE DES COL MAN SEDUC TCH PRM 10ml           11   
1  20998  77.557  QDB BASE LIQ SUPERMAT COR 06 Q 30ml RPCK            1   
2  20858  74.103            GLAMOUR DES COL SEC BL 75ml V4            5   
3   5699  47.950                          ZAAD EDP 95ml V6           12   
4  20993  50.297               ESTJ DEM LILY ESSENCE 4x4ml            2   

     Ciclo  
0  C202307  
1  C202405  
2  C202409  
3  C202406  
4  C202416

In [46]:
#df_venda_diaria['Ciclo'] = df_venda_diaria['Ciclo'].str.replace("C","C20") 

df_venda_diaria = df_venda_diaria.rename(columns={'VENDAS_CICLO':'Vendas_Total'})

df_venda_diaria.head()

PDV     SKU                                 DESCRICAO Vendas_Total  \
0  12522  51.944     COFFEE DES COL MAN SEDUC TCH PRM 10ml           11   
1  20998  77.557  QDB BASE LIQ SUPERMAT COR 06 Q 30ml RPCK            1   
2  20858  74.103            GLAMOUR DES COL SEC BL 75ml V4            5   
3   5699  47.950                          ZAAD EDP 95ml V6           12   
4  20993  50.297               ESTJ DEM LILY ESSENCE 4x4ml            2   

     Ciclo  
0  C202307  
1  C202405  
2  C202409  
3  C202406  
4  C202416

In [47]:
df_venda_diaria['Vendas_Total'] = df_venda_diaria['Vendas_Total'].str.replace(',', '.', regex=False)

df_venda_diaria['Vendas_Total'] = df_venda_diaria['Vendas_Total'].astype('float')

df_venda_diaria['Vendas_Total'] = round(df_venda_diaria['Vendas_Total'],0)

df_venda_diaria['Vendas_Total'] = df_venda_diaria['Vendas_Total'].astype(str)

df_venda_diaria['Vendas_Total'] = (
    df_venda_diaria['Vendas_Total']
    .str.replace('.0', '', regex=False)
    .str.replace('.', '', regex=False)
    .astype('Int64')
)


df_venda_diaria.head()

PDV     SKU                                 DESCRICAO  Vendas_Total  \
0  12522  51.944     COFFEE DES COL MAN SEDUC TCH PRM 10ml            11   
1  20998  77.557  QDB BASE LIQ SUPERMAT COR 06 Q 30ml RPCK             1   
2  20858  74.103            GLAMOUR DES COL SEC BL 75ml V4             5   
3   5699  47.950                          ZAAD EDP 95ml V6            12   
4  20993  50.297               ESTJ DEM LILY ESSENCE 4x4ml             2   

     Ciclo  
0  C202307  
1  C202405  
2  C202409  
3  C202406  
4  C202416

In [48]:
df_venda_diaria[(df_venda_diaria['PDV']==14668) & (df_venda_diaria['SKU']=='85096')]

Empty DataFrame
Columns: [PDV, SKU, DESCRICAO, Vendas_Total, Ciclo]
Index: []

In [49]:
df_venda_diaria2 = df_venda_diaria.pivot_table(
    index=["PDV", "SKU", "DESCRICAO"],
    columns="Ciclo",
    values="Vendas_Total",
    fill_value=0
).reset_index()

# Se quiser, reorganize as colunas colocando os ciclos ao final
df_venda_diaria.columns.name = None

df_venda_diaria.head()

PDV     SKU                                 DESCRICAO  Vendas_Total  \
0  12522  51.944     COFFEE DES COL MAN SEDUC TCH PRM 10ml            11   
1  20998  77.557  QDB BASE LIQ SUPERMAT COR 06 Q 30ml RPCK             1   
2  20858  74.103            GLAMOUR DES COL SEC BL 75ml V4             5   
3   5699  47.950                          ZAAD EDP 95ml V6            12   
4  20993  50.297               ESTJ DEM LILY ESSENCE 4x4ml             2   

     Ciclo  
0  C202307  
1  C202405  
2  C202409  
3  C202406  
4  C202416

In [50]:
df_venda_diaria.columns

Index(['PDV', 'SKU', 'DESCRICAO', 'Vendas_Total', 'Ciclo'], dtype='object')

In [51]:
df_venda_diaria

PDV     SKU                                 DESCRICAO  \
0        12522  51.944     COFFEE DES COL MAN SEDUC TCH PRM 10ml   
1        20998  77.557  QDB BASE LIQ SUPERMAT COR 06 Q 30ml RPCK   
2        20858  74.103            GLAMOUR DES COL SEC BL 75ml V4   
3         5699  47.950                          ZAAD EDP 95ml V6   
4        20993  50.297               ESTJ DEM LILY ESSENCE 4x4ml   
...        ...     ...                                       ...   
1663315  20996  83.039                 QUASAR DES COL RUSH 100ml   
1663316  20970  52.025           BOTI BABY SAB LIQ GLIC V2 400ml   
1663317  20996  93.069  LA PIEL D/COL SPR CP PER AMBR DOUR 200ml   
1663318  13427  51.279         MAKE B BAS LIQ C/ GLYC TX 140 30g   
1663319  21278  52.014    CJ FLAC OUI EDP ICONIQUE INTENSE 3x1ml   

         Vendas_Total    Ciclo  
0                  11  C202307  
1                   1  C202405  
2                   5  C202409  
3                  12  C202406  
4                   2  C202416  
...               ...      ...  
1663315             1  C202415  
1663316             6  C202511  
1663317            10  C202414  
1663318             1  C202309  
1663319             2  C202511  

[1663320 rows x 5 columns]

In [52]:
df_final[['CICLO SIMILAR','PRODUTO SIMILAR','PDV']].dtypes

CICLO SIMILAR      object
PRODUTO SIMILAR     Int64
PDV                 int64
dtype: object

In [53]:
df_final = pd.merge(left=df_final, right=filtered_calendario[['Ciclo','INICIO CICLO','FIM CICLO','DURAÇÃO','match','dias_ate_inicio']], right_on='match',left_on='MATCH',how='left')
df_final.shape

(76, 61)

In [54]:
df_final.head()

PRODUTO LANÇAMENTO                            DESCRIÇÃO DO LANÇAMENTO  \
0               86116  CUIDE-SE BEM DOCES DELÍRIOS ALGODÃO DOCE BODY ...   
1               86116  CUIDE-SE BEM DOCES DELÍRIOS ALGODÃO DOCE BODY ...   
2               86116  CUIDE-SE BEM DOCES DELÍRIOS ALGODÃO DOCE BODY ...   
3               86116  CUIDE-SE BEM DOCES DELÍRIOS ALGODÃO DOCE BODY ...   
4               86116  CUIDE-SE BEM DOCES DELÍRIOS ALGODÃO DOCE BODY ...   

   PRODUTO SIMILAR                                  DESCRIÇÃO SIMILAR  \
0            58363  Body Splash Desodrante Colônia Cuide-se Bem Nu...   
1            58363  Body Splash Desodrante Colônia Cuide-se Bem Nu...   
2            58363  Body Splash Desodrante Colônia Cuide-se Bem Nu...   
3            58363  Body Splash Desodrante Colônia Cuide-se Bem Nu...   
4            58363  Body Splash Desodrante Colônia Cuide-se Bem Nu...   

  CICLO SIMILAR FOCO  IAF   CATEGORIA         MARCA % CONSUMIDOR  ... C202513  \
0       C202506  Não  Não  PERFUMARIA  CUIDE-SE BEM            -  ...     4.0   
1       C202506  Não  Não  PERFUMARIA  CUIDE-SE BEM            -  ...    12.0   
2       C202506  Não  Não  PERFUMARIA  CUIDE-SE BEM            -  ...     3.0   
3       C202506  Não  Não  PERFUMARIA  CUIDE-SE BEM            -  ...     2.0   
4       C202506  Não  Não  PERFUMARIA  CUIDE-SE BEM            -  ...     9.0   

  C202514 C202515 CRESCIMENTO    Ciclo  INICIO CICLO  FIM CICLO DURAÇÃO match  \
0     0.0     0.0     -0.1178  C202517    2025-12-01 2025-12-25      25     1   
1     3.0     0.0     -0.1177  C202517    2025-12-01 2025-12-25      25     1   
2     1.0     0.0     -0.0883  C202517    2025-12-01 2025-12-25      25     1   
3     0.0     0.0     -0.1160  C202517    2025-12-01 2025-12-25      25     1   
4     0.0     0.0     -0.1009  C202517    2025-12-01 2025-12-25      25     1   

  dias_ate_inicio  
0              45  
1              45  
2              45  
3              45  
4              45  

[5 rows x 61 columns]

In [55]:
df_final = pd.merge(left=df_final, right=calendario[['Ciclo','INICIO CICLO','FIM CICLO','DURAÇÃO']], right_on='Ciclo',left_on='CICLO SIMILAR',how='left')
df_final.shape

df_final = df_final.drop_duplicates()

In [56]:

df_venda_diaria = df_venda_diaria.rename(columns={'Vendas_Total':'Vendas Ciclo Lançamento'})
df_venda_diaria.head()

PDV     SKU                                 DESCRICAO  \
0  12522  51.944     COFFEE DES COL MAN SEDUC TCH PRM 10ml   
1  20998  77.557  QDB BASE LIQ SUPERMAT COR 06 Q 30ml RPCK   
2  20858  74.103            GLAMOUR DES COL SEC BL 75ml V4   
3   5699  47.950                          ZAAD EDP 95ml V6   
4  20993  50.297               ESTJ DEM LILY ESSENCE 4x4ml   

   Vendas Ciclo Lançamento    Ciclo  
0                       11  C202307  
1                        1  C202405  
2                        5  C202409  
3                       12  C202406  
4                        2  C202416

In [57]:
df_final['CICLO SIMILAR'] = df_final['CICLO SIMILAR'].fillna('0')
df_final['CICLO SIMILAR'] 

0       C202506
28      C202506
56      C202506
84      C202506
112     C202506
         ...   
1988    C202506
2016    C202506
2044    C202506
2072    C202506
2100    C202506
Name: CICLO SIMILAR, Length: 76, dtype: object

In [58]:
df_final[['CICLO SIMILAR','PRODUTO SIMILAR','PDV']].head()

CICLO SIMILAR  PRODUTO SIMILAR    PDV
0         C202506            58363  12522
28        C202506            58363  12817
56        C202506            58363  12818
84        C202506            58363  12820
112       C202506            58363  12823

In [59]:


df_final['PRODUTO SIMILAR'] = df_final['PRODUTO SIMILAR'].astype('Int64')



In [60]:
df_final.columns

Index(['PRODUTO LANÇAMENTO', 'DESCRIÇÃO DO LANÇAMENTO', 'PRODUTO SIMILAR',
       'DESCRIÇÃO SIMILAR', 'CICLO SIMILAR', 'FOCO', 'IAF', 'CATEGORIA',
       'MARCA', '% CONSUMIDOR', 'MECANICA CONSUMIDOR', '% REVENDEDOR',
       'MECANICA REVENDEDOR', 'TIPO DE PRODUTO', 'MATCH', 'PDV', 'CANAL',
       'DESCRIÇÃO PDV', 'PDV DESC', 'UF', 'ANALISTA', 'SUPERVISOR', 'STATUS',
       'ANALISTA EUD', 'SKU', 'curva', 'categoria', 'proj_mar', 'proj_mar+1',
       'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO', 'PEDIDO PENDENTE',
       'DDV PREVISTO', 'preço', 'SKU_FINAL', 'DESCRICAO', 'C202415', 'C202416',
       'C202417', 'C202501', 'C202502', 'C202503', 'C202504', 'C202505',
       'C202506', 'C202507', 'C202508', 'C202509', 'C202510', 'C202511',
       'C202512', 'C202513', 'C202514', 'C202515', 'CRESCIMENTO', 'Ciclo_x',
       'INICIO CICLO_x', 'FIM CICLO_x', 'DURAÇÃO_x', 'match',
       'dias_ate_inicio', 'Ciclo_y', 'INICIO CICLO_y', 'FIM CICLO_y',
       'DURAÇÃO_y'],
      dtype='object')

In [61]:
df_venda_diaria['SKU'] = df_venda_diaria['SKU'].astype('str')

df_venda_diaria['SKU'] = df_venda_diaria['SKU'].str.replace('.','')

df_venda_diaria.head()

PDV    SKU                                 DESCRICAO  \
0  12522  51944     COFFEE DES COL MAN SEDUC TCH PRM 10ml   
1  20998  77557  QDB BASE LIQ SUPERMAT COR 06 Q 30ml RPCK   
2  20858  74103            GLAMOUR DES COL SEC BL 75ml V4   
3   5699  47950                          ZAAD EDP 95ml V6   
4  20993  50297               ESTJ DEM LILY ESSENCE 4x4ml   

   Vendas Ciclo Lançamento    Ciclo  
0                       11  C202307  
1                        1  C202405  
2                        5  C202409  
3                       12  C202406  
4                        2  C202416

In [62]:
df_final['PRODUTO SIMILAR'] = df_final['PRODUTO SIMILAR'].astype('str')

In [63]:
df_final = pd.merge(left=df_final, right = df_venda_diaria[['PDV','SKU','Ciclo','Vendas Ciclo Lançamento']], right_on=['Ciclo','SKU','PDV'],left_on=['CICLO SIMILAR','PRODUTO SIMILAR','PDV'],how='left')

df_final = df_final.drop_duplicates()

In [64]:
df_final = df_final[df_final['PRODUTO LANÇAMENTO'].notna()]
df_final['Vendas Ciclo Lançamento'] = df_final['Vendas Ciclo Lançamento'].fillna(0)


In [65]:
df_final['PDV'].value_counts().min()

np.int64(1)

In [66]:
df_final.columns[29:46]

Index(['ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO', 'PEDIDO PENDENTE',
       'DDV PREVISTO', 'preço', 'SKU_FINAL', 'DESCRICAO', 'C202415', 'C202416',
       'C202417', 'C202501', 'C202502', 'C202503', 'C202504', 'C202505',
       'C202506', 'C202507'],
      dtype='object')

In [67]:
df_jacobina = pd.read_excel(r"../../SUPRIMENTOS/BD_LANÇAMENTOS/BOT/arquivos usados por todos os lançamentos/draft unificado.xlsx")

In [68]:
df_jacobina = df_jacobina[['PDV', 'SKU','202408', '202409',
       '202410', '202411', '202412', '202413', '202414', '202415', '202416',
       '202417', '202501', '202502', '202503', '202504', '202505', '202506',
       '202507']]

In [69]:
ciclos = [
    '202408', '202409', '202410', '202411', '202412', '202413',
    '202414', '202415', '202416', '202417', '202501', '202502',
    '202503', '202504', '202505', '202506', '202507']

df_jacobina[ciclos] = df_jacobina[ciclos].fillna(0)

In [70]:
df_jacobina.head()

PDV    SKU  202408  202409  202410  202411  202412  202413  202414  \
0  24269  49014       1       0       5       1       1       1       2   
1  24268  49014       1       0       4       4       2       5       1   
2  24269  49016      36       3       1       1       1       0      14   
3  24268  49016      12       3       1       2       2       2       0   
4  24269  48141      32       2       3      95       3       2      41   

   202415  202416  202417  202501  202502  202503  202504  202505  202506  \
0       2       1       1       3       0       4       0       2       1   
1       3       4       4       3       0       2       4       2       0   
2       2       2       1       1      19       1       2       2      10   
3       0       3      11       4       3       0       4       2       1   
4       3       3       1       1       1       0      67       4      10   

   202507  
0       0  
1       1  
2       0  
3       0  
4       2

In [71]:
df_final['PRODUTO SIMILAR'] = df_final['PRODUTO SIMILAR'].astype('Int64')

df_final.head()

PRODUTO LANÇAMENTO                            DESCRIÇÃO DO LANÇAMENTO  \
0               86116  CUIDE-SE BEM DOCES DELÍRIOS ALGODÃO DOCE BODY ...   
1               86116  CUIDE-SE BEM DOCES DELÍRIOS ALGODÃO DOCE BODY ...   
2               86116  CUIDE-SE BEM DOCES DELÍRIOS ALGODÃO DOCE BODY ...   
3               86116  CUIDE-SE BEM DOCES DELÍRIOS ALGODÃO DOCE BODY ...   
4               86116  CUIDE-SE BEM DOCES DELÍRIOS ALGODÃO DOCE BODY ...   

   PRODUTO SIMILAR                                  DESCRIÇÃO SIMILAR  \
0            58363  Body Splash Desodrante Colônia Cuide-se Bem Nu...   
1            58363  Body Splash Desodrante Colônia Cuide-se Bem Nu...   
2            58363  Body Splash Desodrante Colônia Cuide-se Bem Nu...   
3            58363  Body Splash Desodrante Colônia Cuide-se Bem Nu...   
4            58363  Body Splash Desodrante Colônia Cuide-se Bem Nu...   

  CICLO SIMILAR FOCO  IAF   CATEGORIA         MARCA % CONSUMIDOR  ...  \
0       C202506  Não  Não  PERFUMARIA  CUIDE-SE BEM            -  ...   
1       C202506  Não  Não  PERFUMARIA  CUIDE-SE BEM            -  ...   
2       C202506  Não  Não  PERFUMARIA  CUIDE-SE BEM            -  ...   
3       C202506  Não  Não  PERFUMARIA  CUIDE-SE BEM            -  ...   
4       C202506  Não  Não  PERFUMARIA  CUIDE-SE BEM            -  ...   

  DURAÇÃO_x match dias_ate_inicio  Ciclo_y  INICIO CICLO_y  FIM CICLO_y  \
0        25     1              45  C202506      2025-04-14   2025-05-11   
1        25     1              45  C202506      2025-04-14   2025-05-11   
2        25     1              45  C202506      2025-04-14   2025-05-11   
3        25     1              45  C202506      2025-04-14   2025-05-11   
4        25     1              45  C202506      2025-04-14   2025-05-11   

  DURAÇÃO_y  SKU_y    Ciclo Vendas Ciclo Lançamento  
0        28  58363  C202506                      40  
1        28  58363  C202506                     102  
2        28  58363  C202506                      15  
3        28  58363  C202506                      13  
4        28  58363  C202506                      24  

[5 rows x 68 columns]

In [72]:
df_final = pd.merge(left=df_final,right=df_jacobina,left_on=['PRODUTO SIMILAR','PDV'],right_on=['SKU','PDV'],how='left')

In [73]:
# Gera pares de colunas: coluna estática ↔ coluna de histórico
pares_validos = [
    (ciclo, f'Histórico de Vendas do Ciclo {ciclo}')
    for ciclo in ciclos
    if ciclo in df_final.columns and f'Histórico de Vendas do Ciclo {ciclo}' in df_final.columns
]

# Separa os nomes das colunas
colunas_estaticas = [c[0] for c in pares_validos]
colunas_historico = [c[1] for c in pares_validos]

# Aplica a regra: se valor na coluna estática for maior, sobrescreve no histórico
for col_estatica, col_hist in zip(colunas_estaticas, colunas_historico):
    df_final[col_hist] = df_final[col_estatica].where(
        df_final[col_estatica] > df_final[col_hist],
        df_final[col_hist]
    )


In [74]:
df_final = df_final.fillna(0)

In [75]:
# VERIFICAR SE TEM OS 17 CICLOS DE VENDA
df_final.columns[36:54]

Index(['C202415', 'C202416', 'C202417', 'C202501', 'C202502', 'C202503',
       'C202504', 'C202505', 'C202506', 'C202507', 'C202508', 'C202509',
       'C202510', 'C202511', 'C202512', 'C202513', 'C202514', 'C202515'],
      dtype='object')

In [76]:
# Suponha que os meses estão nas colunas 10 a 26 (17 colunas = 17 meses)
colunas_mensais = df_final.columns[36:54]
# Passo 1: Soma todas as linhas (itens) por mês → resultado: total por mês
soma_mensal = df_final[colunas_mensais].sum()

# Passo 2: Calcula a variação percentual de um mês para o outro
variacao_mensal = soma_mensal.pct_change()
variacao_mensal = variacao_mensal.dropna()

variacao_mensal = variacao_mensal[np.isfinite(variacao_mensal)]

# Passo 3: Calcula a média da variação (ignorando o primeiro NaN)
media_variacao = variacao_mensal[1:].mean()

# Calcula média e desvio padrão
media = variacao_mensal.mean()
desvio = variacao_mensal.std()

# Define limite (ex: 2 desvios padrão)
limite_superior = media + 2 * desvio
limite_inferior = media - 2 * desvio

# Filtra dados dentro do limite
filtro = variacao_mensal.between(limite_inferior, limite_superior)
df_filtrado = variacao_mensal[filtro]
CRESCIMENTO = round(df_filtrado.mean(),4)

CRESCIMENTO = 0.2 if CRESCIMENTO < 0.2 else CRESCIMENTO

df_final['CRESCIMENTO_GERAL'] = CRESCIMENTO

CRESCIMENTO


0.2

In [77]:
df_final = df_final.drop(columns='Ciclo_y')

df_final = df_final.rename(columns={'Ciclo_x': 'Ciclo',	'INICIO CICLO_x': 'INICIO CICLO',	'FIM CICLO_x':'FIM CICLO' ,'DURAÇÃO_x':'DURAÇÃO',
                                    	'INICIO CICLO_y': 'INICIO CICLO SIMILAR' ,	'FIM CICLO_y': 'FIM CICLO SIMILAR','DURAÇÃO_y':'DURAÇÃO CICLO SIMILAR'})

In [78]:
# VERIFICAR SE AS 6 ULTIMAS COLUNAS SÃO DE VENDA CICLO
df_final.columns[47:54]

Index(['C202509', 'C202510', 'C202511', 'C202512', 'C202513', 'C202514',
       'C202515'],
      dtype='object')

In [79]:
VENDA_SIMILAR_6_MESES= df_final.columns[47:54]
df_final['Pico Vendas Similar Ultimos 6 ciclos'] = df_final[VENDA_SIMILAR_6_MESES].max(axis=1)

df_final['Pico Vendas Similar Ultimos 6 ciclos'] = df_final['Pico Vendas Similar Ultimos 6 ciclos'].fillna(0)

df_final['MEDIANA DO HISTÓRICO'] = df_final[colunas_mensais].median(axis=1, skipna=True)




In [80]:
df_final[colunas_mensais].median(axis=1, skipna=True)


0     0.0
1     1.0
2     0.0
3     0.0
4     0.0
     ... 
71    0.0
72    0.0
73    0.0
74    0.0
75    0.0
Length: 76, dtype: float64

In [81]:
medi = df_final.groupby(['CANAL','UF','PRODUTO LANÇAMENTO'])['MEDIANA DO HISTÓRICO'].max().reset_index()
medi = medi.rename(columns={'MEDIANA DO HISTÓRICO':'med_por_canal'})
medi

CANAL  UF  PRODUTO LANÇAMENTO  med_por_canal
0    CD  AL               86116            0.0
1   HIB  AL               86116            1.0
2   HIB  BA               86116            1.0
3   HIB  SE               86116            0.5
4    LJ  AL               86116            1.0
5    LJ  BA               86116            0.5
6    LJ  SE               86116            0.5
7    VD  AL               86116            4.5
8    VD  BA               86116            2.0
9    VD  SE               86116            4.0

In [82]:
df_dourado = pd.read_excel(r"../../SUPRIMENTOS/BD_LANÇAMENTOS/BOT/arquivos usados por todos os lançamentos/compilado de vendas.xlsx")

df_dourado['Data de venda'] = pd.to_datetime(df_dourado['Data de venda'], dayfirst=True)

df_dourado['de para pdv'] = df_dourado['de para pdv'].astype(str)

df_dourado['de para pdv'] = df_dourado['de para pdv'].str.replace(r'\.0$', '', regex=True)

# 'Dia' já está em formato datetime, então renomeamos para 'Data' diretamente
# ou apenas usamos 'Dia' como referência de data

# Ordena o DataFrame para garantir que a cumulativa funcione corretamente
df_venda_diaria = df_venda_diaria.sort_values(by=['PDV', 'SKU', 'Ciclo'])

# Calcula a quantidade acumulada até o dia para cada grupo
df_dourado['Quantidade Acumulada dourado'] = (
    df_dourado
    .groupby(['de para pdv', 'sku'])['Quantidade Vendida']
    .cumsum()
)  # acumulado por grupo até a data da linha

df_dourado = pd.merge(left=df_dourado,right=calendario[['Date','Ciclo']],left_on='Data de venda',right_on='Date',how='inner')



df_dourado_agrupado = df_dourado.groupby(['de para pdv','sku','Ciclo'])['Quantidade Acumulada dourado'].max().reset_index()

df_dourado_agrupado = df_dourado_agrupado.rename(columns={'Ciclo':'Ciclo dourado'})



In [83]:
df_final['PDV'] = df_final['PDV'].astype(str)
df_final['PDV'].head()

0    12522
1    12817
2    12818
3    12820
4    12823
Name: PDV, dtype: object

In [84]:
df_final = pd.merge(left=df_final, right = df_dourado_agrupado, right_on=['Ciclo dourado','sku','de para pdv'],left_on=['CICLO SIMILAR','PRODUTO SIMILAR','PDV'],how='left')

df_final['Quantidade Acumulada dourado'] = df_final['Quantidade Acumulada dourado'].fillna(0)


df_final['Vendas Ciclo Lançamento'] = np.where(df_final['Quantidade Acumulada dourado'] > 0, df_final['Quantidade Acumulada dourado'], df_final['Vendas Ciclo Lançamento'])

df_final = df_final.drop(columns='Quantidade Acumulada dourado')


df_final = df_final.drop(columns='Ciclo dourado')

In [85]:
df_depara_vdc = pd.read_excel(r"../../SUPRIMENTOS/BD_LANÇAMENTOS/BOT/arquivos usados por todos os lançamentos/Filiais - Vitoria da Conquista 4.xlsx")

df_depara_vdc.head()

CP VIVA BEM  Protheus  PDVDEPARA.Practico        Canal  \
0         3559   70101.0             23713.0  MATRIZ - LJ   
1         7292   70103.0             23712.0         LOJA   
2         8708   70102.0             23711.0           VD   
3         8931       NaN             23710.0          NaN   
4        11191   70108.0             23709.0         LOJA   

                                            Endereço                CNPJ  \
0  Rua Zeferino Correia, nº 17, Centro, CEP 45.00...  14.378.160/0001-83   
1  Al. Rio Branco, nº 373, Centro, Cândido Sales ...  14.378.160/0006-98   
2  Al. Lima Guerra, nº 04, Centro, Vitória da Con...  14.378.160/0005-07   
3  Avenida Rosa Cruz, nº 80, Hiper B Preço Loja B...  14.378.160/0008-50   
4  Av. Juracy Magalhães, nº 3340, Shopping Conqui...  14.378.160/0009-30   

         CNPJ Locação  
0  14.378.160/0001-83  
1  14.378.160/0006-98  
2  14.378.160/0001-83  
3  14.378.160/0008-50  
4  14.378.160/0001-83

In [86]:
df_final['PRODUTO SIMILAR'] = df_final['PRODUTO SIMILAR'].astype('Int64')

In [87]:

# Cálculo do crescimento
crescimento_final = df_final['CRESCIMENTO_GERAL'] + df_final['CRESCIMENTO']
crescimento_final = crescimento_final.clip(lower=0.2, upper=0.8)  # limita entre 0 e 0.8
df_final['CRESCIMENTO_FINAL'] = crescimento_final

df_final['CRESCIMENTO_FINAL'] = np.where(df_final['CRESCIMENTO_FINAL'].isna(),df_final['CRESCIMENTO_GERAL'],df_final['CRESCIMENTO_FINAL'])

df_final['CRESCIMENTO_FINAL'] = df_final['CRESCIMENTO_FINAL'].fillna(0)

df_final['MEDIANA DO HISTÓRICO'] = df_final['MEDIANA DO HISTÓRICO'].fillna(0)

# Corrige mediana do histórico onde for zero
df_final['MEDIANA DO HISTÓRICO'] = np.where(
    df_final['MEDIANA DO HISTÓRICO'] == 0,
    0,
    df_final['MEDIANA DO HISTÓRICO']
)

df_final['MEDIANA DO HISTÓRICO'] = df_final['MEDIANA DO HISTÓRICO'].fillna(0)



# Cálculo do PV GINSENG
pv_crescimento = (df_final['CRESCIMENTO_FINAL']+1) * df_final['Vendas Ciclo Lançamento']
pv_mediana = (df_final['CRESCIMENTO_FINAL'] + 1) * df_final['MEDIANA DO HISTÓRICO']

df_final['PV GINSENG'] = np.where(
    pv_crescimento < df_final['MEDIANA DO HISTÓRICO'],
    pv_mediana.round(0),
    pv_crescimento.round(0)
)

# Se PV GINSENG for NA, substitui pela média por canal
df_final['PV GINSENG'] = df_final['PV GINSENG'].fillna(0)

df_final['PV GINSENG'] = df_final['PV GINSENG'].round(0).astype(int)

df_final.shape


(76, 92)

In [88]:
# verificar as vendas dos ciclos
print(df_final.columns[68:85])

Index(['202408', '202409', '202410', '202411', '202412', '202413', '202414',
       '202415', '202416', '202417', '202501', '202502', '202503', '202504',
       '202505', '202506', '202507'],
      dtype='object')


In [89]:
import re

# identificar colunas de ciclo puro (ex: '202407')
colunas_ciclo_puro = [col for col in df_final.columns[68:85]]

for col in colunas_ciclo_puro:
    col_hist = f'C{col}'
    if col_hist in df_final.columns:
        # mantém o maior valor entre a coluna histórica e a pura
        df_final[col_hist] = df_final[[col_hist, col]].max(axis=1)

# remove as colunas puras
if colunas_ciclo_puro:
    df_final.drop(columns=colunas_ciclo_puro, inplace=True)

df_final.columns

Index(['PRODUTO LANÇAMENTO', 'DESCRIÇÃO DO LANÇAMENTO', 'PRODUTO SIMILAR',
       'DESCRIÇÃO SIMILAR', 'CICLO SIMILAR', 'FOCO', 'IAF', 'CATEGORIA',
       'MARCA', '% CONSUMIDOR', 'MECANICA CONSUMIDOR', '% REVENDEDOR',
       'MECANICA REVENDEDOR', 'TIPO DE PRODUTO', 'MATCH', 'PDV', 'CANAL',
       'DESCRIÇÃO PDV', 'PDV DESC', 'UF', 'ANALISTA', 'SUPERVISOR', 'STATUS',
       'ANALISTA EUD', 'SKU_x', 'curva', 'categoria', 'proj_mar', 'proj_mar+1',
       'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO', 'PEDIDO PENDENTE',
       'DDV PREVISTO', 'preço', 'SKU_FINAL', 'DESCRICAO', 'C202415', 'C202416',
       'C202417', 'C202501', 'C202502', 'C202503', 'C202504', 'C202505',
       'C202506', 'C202507', 'C202508', 'C202509', 'C202510', 'C202511',
       'C202512', 'C202513', 'C202514', 'C202515', 'CRESCIMENTO', 'Ciclo',
       'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO', 'match', 'dias_ate_inicio',
       'INICIO CICLO SIMILAR', 'FIM CICLO SIMILAR', 'DURAÇÃO CICLO SIMILAR',
       'SKU_y', 'Ciclo', 'Vend

In [90]:
df_final.columns[49:54]

Index(['C202511', 'C202512', 'C202513', 'C202514', 'C202515'], dtype='object')

In [91]:
df_final['Pico Vendas Similar Ultimos 6 ciclos'] = df_final[VENDA_SIMILAR_6_MESES].max(axis=1)

In [92]:
df_final = df_final.rename(columns={df_final.columns[49]: "C-4", df_final.columns[50]: "C-3",df_final.columns[51]: "C-2",df_final.columns[52]: "C-1",df_final.columns[53]:'VENDAS CICLO ATUAL'})


In [93]:
df_final.columns = df_final.columns.str.upper()

df_final.drop(columns=df_final.filter(regex='_Y').columns, inplace=True)

df_final.columns

Index(['PRODUTO LANÇAMENTO', 'DESCRIÇÃO DO LANÇAMENTO', 'PRODUTO SIMILAR',
       'DESCRIÇÃO SIMILAR', 'CICLO SIMILAR', 'FOCO', 'IAF', 'CATEGORIA',
       'MARCA', '% CONSUMIDOR', 'MECANICA CONSUMIDOR', '% REVENDEDOR',
       'MECANICA REVENDEDOR', 'TIPO DE PRODUTO', 'MATCH', 'PDV', 'CANAL',
       'DESCRIÇÃO PDV', 'PDV DESC', 'UF', 'ANALISTA', 'SUPERVISOR', 'STATUS',
       'ANALISTA EUD', 'SKU_X', 'CURVA', 'CATEGORIA', 'PROJ_MAR', 'PROJ_MAR+1',
       'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO', 'PEDIDO PENDENTE',
       'DDV PREVISTO', 'PREÇO', 'SKU_FINAL', 'DESCRICAO', 'C202415', 'C202416',
       'C202417', 'C202501', 'C202502', 'C202503', 'C202504', 'C202505',
       'C202506', 'C202507', 'C202508', 'C202509', 'C202510', 'C-4', 'C-3',
       'C-2', 'C-1', 'VENDAS CICLO ATUAL', 'CRESCIMENTO', 'CICLO',
       'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO', 'MATCH', 'DIAS_ATE_INICIO',
       'INICIO CICLO SIMILAR', 'FIM CICLO SIMILAR', 'DURAÇÃO CICLO SIMILAR',
       'CICLO', 'VENDAS CICLO LANÇA

In [94]:
df_final = df_final.rename(columns={'MARCA_X':'MARCA'})

In [95]:
df_final.shape

(76, 74)

In [96]:
df_final[['C-4', 'C-3', 'C-2', 'C-1', 'VENDAS CICLO ATUAL']] = df_final[['C-4', 'C-3', 'C-2', 'C-1', 'VENDAS CICLO ATUAL']].fillna(0)

In [97]:
df_final = df_final.loc[:, ~df_final.columns.duplicated()]

colunas_desejadas = [
    'SUPERVISOR',
    'ANALISTA',
    'CANAL',
    'UF',
    'PDV',
    'DESCRIÇÃO PDV',
    'PRODUTO LANÇAMENTO',
    'DESCRIÇÃO DO LANÇAMENTO',
    'MARCA',
    'CURVA',
    'CATEGORIA',
    '% CONSUMIDOR',
    'MECANICA CONSUMIDOR',
    '% REVENDEDOR',
    'MECANICA REVENDEDOR',
    'TIPO DE PRODUTO',
    'IAF',
    'FOCO',
    'PRODUTO SIMILAR',
    'DESCRIÇÃO SIMILAR',
    'CICLO SIMILAR',
    'VENDAS CICLO LANÇAMENTO',
    'C-4',
    'C-3',
    'C-2',
    'C-1',
    'VENDAS CICLO ATUAL',
    'PICO VENDAS SIMILAR ULTIMOS 6 CICLOS',
    'PV GINSENG'
]

df_final = df_final.reindex(columns=colunas_desejadas)

colunas_filtradas = [col for col in colunas_desejadas if col in df_final.columns]
df_final = df_final[colunas_filtradas]


In [98]:
df_final['SUGESTÃO METASELLIN'] = ''
df_final['SUGESTÃO ABASTECIMENTO'] = ''
df_final['SUGESTÃO COMERCIAL'] = ''


In [99]:
df_pdv_origi['PDV'] = df_pdv_origi['PDV'].astype(str)

df_pdv_origi['PDV'].head()

df_pdv_origi = df_pdv_origi.rename(columns={'UF':'UF_CERTO'})

In [100]:
#adicionando o UF correto ao fim do script
df_final= pd.merge(df_final,df_pdv_origi[['UF_CERTO','PDV']],on='PDV',how='inner')

In [101]:
df_final['UF']= df_final['UF_CERTO']

df_final = df_final.drop(columns=['UF_CERTO'])

df_final.head()

SUPERVISOR   ANALISTA CANAL  UF    PDV    DESCRIÇÃO PDV  \
0  Efigênia Herculano       LUAN    LJ  AL  12522  MACEIO SHOP EXP   
1      Maxwell Vieira  JEFFERSON    LJ  AL  12817   SHOPPING PATIO   
2      Maxwell Vieira   VINICIUS    LJ  AL  12818      GB SERRARIA   
3      Maxwell Vieira    ADRIELY    LJ  AL  12820         ATACADÃO   
4  Efigênia Herculano    ADRIELY    LJ  AL  12823      PONTA VERDE   

   PRODUTO LANÇAMENTO                            DESCRIÇÃO DO LANÇAMENTO  \
0               86116  CUIDE-SE BEM DOCES DELÍRIOS ALGODÃO DOCE BODY ...   
1               86116  CUIDE-SE BEM DOCES DELÍRIOS ALGODÃO DOCE BODY ...   
2               86116  CUIDE-SE BEM DOCES DELÍRIOS ALGODÃO DOCE BODY ...   
3               86116  CUIDE-SE BEM DOCES DELÍRIOS ALGODÃO DOCE BODY ...   
4               86116  CUIDE-SE BEM DOCES DELÍRIOS ALGODÃO DOCE BODY ...   

          MARCA CURVA  ...   C-4   C-3   C-2  C-1 VENDAS CICLO ATUAL  \
0  CUIDE-SE BEM     A  ...   7.0   5.0   4.0  0.0                0.0   
1  CUIDE-SE BEM     B  ...  39.0   7.0  12.0  3.0                0.0   
2  CUIDE-SE BEM     B  ...   5.0   1.0   3.0  1.0                0.0   
3  CUIDE-SE BEM     B  ...   8.0   0.0   2.0  0.0                0.0   
4  CUIDE-SE BEM     A  ...  14.0  11.0   9.0  0.0                0.0   

  PICO VENDAS SIMILAR ULTIMOS 6 CICLOS PV GINSENG SUGESTÃO METASELLIN  \
0                                  8.0         48                       
1                                 39.0        122                       
2                                  5.0         18                       
3                                  8.0         16                       
4                                 14.0         29                       

   SUGESTÃO ABASTECIMENTO SUGESTÃO COMERCIAL  
0                                             
1                                             
2                                             
3                                             
4                                             

[5 rows x 32 columns]

In [102]:
df_final.columns

Index(['SUPERVISOR', 'ANALISTA', 'CANAL', 'UF', 'PDV', 'DESCRIÇÃO PDV',
       'PRODUTO LANÇAMENTO', 'DESCRIÇÃO DO LANÇAMENTO', 'MARCA', 'CURVA',
       'CATEGORIA', '% CONSUMIDOR', 'MECANICA CONSUMIDOR', '% REVENDEDOR',
       'MECANICA REVENDEDOR', 'TIPO DE PRODUTO', 'IAF', 'FOCO',
       'PRODUTO SIMILAR', 'DESCRIÇÃO SIMILAR', 'CICLO SIMILAR',
       'VENDAS CICLO LANÇAMENTO', 'C-4', 'C-3', 'C-2', 'C-1',
       'VENDAS CICLO ATUAL', 'PICO VENDAS SIMILAR ULTIMOS 6 CICLOS',
       'PV GINSENG', 'SUGESTÃO METASELLIN', 'SUGESTÃO ABASTECIMENTO',
       'SUGESTÃO COMERCIAL'],
      dtype='object')

In [103]:

# lista de colunas numéricas
numeric_cols = [
    'VENDAS CICLO LANÇAMENTO', 'C-4', 'C-3', 'C-2', 'C-1',
    'VENDAS CICLO ATUAL', 'PICO VENDAS SIMILAR ULTIMOS 6 CICLOS',
    'PV GINSENG', 'SUGESTÃO METASELLIN', 'SUGESTÃO ABASTECIMENTO',
    'SUGESTÃO COMERCIAL'
]

# colunas não numéricas = todas menos as numéricas
non_numeric_cols = [col for col in df_final.columns if col not in numeric_cols]

# agrupar por todas as não numéricas, pegando o máximo das numéricas
df_final_sem_dupli = (
    df_final
    .groupby(non_numeric_cols, as_index=False)[numeric_cols]
    .sum()
)


In [104]:
arquivo_similares.split('\\')[0:-2]

['C:',
 'Users',
 'joao.herculano',
 'GRUPO GINSENG',
 'Assistência Suprimentos - 2025',
 'SUPRIMENTOS',
 'BD_LANÇAMENTOS',
 'BOT',
 'BOT - C17',
 'arquivos para geração da sugestão']

In [105]:
caminho_out =arquivo_similares.split('\\')[0:-2]

resultado_out = "\\".join(caminho_out)
resultado_out

'C:\\Users\\joao.herculano\\GRUPO GINSENG\\Assistência Suprimentos - 2025\\SUPRIMENTOS\\BD_LANÇAMENTOS\\BOT\\BOT - C17\\arquivos para geração da sugestão'

In [106]:
df_final_sem_dupli['CURVA'].value_counts()

CURVA
B    63
A    10
C     2
0     1
Name: count, dtype: int64

In [107]:
df_final_sem_dupli['CURVA'] = df_final_sem_dupli['CURVA'].astype('str')

In [108]:
df_final_sem_dupli['CURVA'] = df_final_sem_dupli['CURVA'].str.replace('0','E')

In [109]:
df_final_sem_dupli['CURVA'].value_counts()

CURVA
B    63
A    10
C     2
E     1
Name: count, dtype: int64

In [110]:
#df_final_sem_dupli.to_excel(f'{resultado_out}\\LANCAMENTO_{hoje}.xlsx',index=False)

In [111]:
# Export to Excel
output_file = f'{resultado_out}\\LANCAMENTO_{hoje}.xlsx'
with pd.ExcelWriter(output_file, engine='openpyxl') as writer:
    df_final_sem_dupli.to_excel(writer, index=False)

# Apply styles
wb = load_workbook(output_file)
ws = wb['Sheet1']

# Style header
header_fill = PatternFill(start_color='366092', end_color='366092', fill_type='solid')  # Light Blue
header_font = Font(color='FFFFFF', bold=True)  # White & Bold

for cell in ws[1]:
    cell.fill = header_fill
    cell.font = header_font

# Style rows: gray/white alternating
gray_fill = PatternFill(start_color='DDDDDD', end_color='DDDDDD', fill_type='solid')  # Light gray

for i, row in enumerate(ws.iter_rows(min_row=2, max_row=ws.max_row), start=2):
    if i % 2 == 0:
        for cell in row:
            cell.fill = gray_fill

# Save styled workbook
wb.save(output_file)